This Notebook will take a Youtube Playlist and convert all videos to MP3:s , which will be stored on a folder on your Google Drive.

In [1]:
#Initialize
import os
def my_mkdirs(folder):
  if os.path.exists(folder)==False:
    os.makedirs(folder)
my_mkdirs('/content/tmp/')

In [ ]:
#NOTE:  you need to download cookies from youtube to your drive folder because of recent Youtubr BS restrictions
#Reinstall youtube_dl because the version on Colab is outdated
!python3 -m pip install --force-reinstall https://github.com/yt-dlp/yt-dlp/archive/master.tar.gz
import yt_dlp as youtube_dl


In [ ]:
#Mount Google Drive
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
# @markdown download video or playlist as audio file mp3
youtube_link = '' # @param {type:'string'}
playlist_start = 1
## @param {type:'number'}
playlist_end = 9999
## @param {type:'number'}

#Extract all videos in YT playlist mp3 files
#Aborting this code is fine if list is latge ( You will keep downloaded mp3:s)
%cd /content/tmp
for playlist_URL in youtube_link.split(','):
  !yt-dlp --cookies /content/drive/MyDrive/ytcookies.txt --playlist-end {playlist_end} --playlist-start {playlist_start} --extract-audio --audio-format mp3 -o "%(title)s.%(ext)s" {playlist_URL}

In [ ]:

# @markdown Download video or playlist as highest video quality mp4
youtube_link = 'https://youtu.be/qxzbh6vPRZg?si=Ov2zBKly95fn-xGr' # @param {type:'string'}
playlist_start = 1
## @param {type:'number'}
playlist_end = 9999
## @param {type:'number'}

#Extract all videos in YT playlist mp3 files
#Aborting this code is fine if list is latge ( You will keep downloaded mp3:s)
%cd /content/drive/MyDrive/Saved from Chrome/
for playlist_URL in youtube_link.split(','):
  !yt-dlp --cookies /content/drive/MyDrive/ytcookies.txt --playlist-end {playlist_end} --playlist-start {playlist_start} --merge-output-format mp4 -f "bestvideo+bestaudio[ext=m4a]/best"  -o "%(title)s.%(ext)s" {playlist_URL}

In [ ]:

# @markdown 🌊 Rapid keyframe processing
# @markdown <br> ------ <br> Extract Keyframes from ALL mp4 / webm videos found on Google Drive
# @markdown <br> Be mindful of Google Drive Terms of Service
# @markdown <br> This cell will process all mp4 videos found under
# @markdown <br> /content/drive/MyDrive/Saved from Chrome/
delete_mp4_when_done = True # @param {type:'boolean'}
# @markdown <br> deleted mp4/webm files will be found under 'trash' in your Google drive
# @markdown <br> -------
# @markdown <br>  (Optional) Add a direct video link to below field.
# @markdown <br>  Multiple links can be written in this field
# @markdown <br> separated by comma.  Like this: <br> ' https:\\\my_video.mp4  ,  https:\\\second_video.webm ,  ....  '
import os
import shutil
!pip install video-kf
!pip install ffmpeg-python
!pip install wget
!pip install moviepy
import wget
import videokf as vf
import time
proc_keyframes=True # @param {type:'boolean'}
proc_audio=False # @param {type:'boolean'}
#def mkdirs(folder):
#  if not os.path.exists(folder):os.makedirs(folder)
#----#
direct_link = '' # @param {type:'string'}
# @markdown The linked videos will be downloaded to the Google drive prior to running the script.
# @markdown <br> This feature is useful for direct processing .webm from 4chan threads into keyframes
use_link = False # @param {type:'boolean'}
if direct_link.find('http')>-1: use_link = True
if use_link:
  %cd '/content/drive/MyDrive/Saved from Chrome/'
  for link in direct_link.split(','):
    if not link.find('http')>-1:continue
    wget.download(link.strip())
    time.sleep(5)
  %cd '/content/'
#-----#
filenames = []
srcpath = '/content/drive/MyDrive/Saved from Chrome/'
destpath = '/content/drive/MyDrive/'
localpath = '/content/'
converted = ''
for filename in os.listdir(f'{srcpath}'):
  if filename.find('.zip')>-1:
    %cd {srcpath}
    !unzip {filename}
    os.remove(filename)
    filename = filename.replace('.zip','')
  for suffix in ['.mp4','.webm']:
    if filename.find(f'{suffix}')>-1: filenames.append(filename)
#Rename the downloaded video to 'tgt0' before running this cell
def my_mkdirs(folder):
  if os.path.exists(folder):shutil.rmtree(folder)
  os.makedirs(folder)
#----#
# @markdown Write a funny name for the folder(s) containing the keyframes
name_keyframes_as='' # @param {type:'string'}
# @markdown Created .zip files will not be overwritten
#NUM_ITEMS = 1 # @param {type:'slider', min:1 , max:20,step:1}
if name_keyframes_as.strip()=='': name_keyframes_as='keyframes'
num = 0
savepath = ''
%cd {localpath}
for filename in filenames:
  tgt_folder = f'/content/tmp'
  my_mkdirs(f'{tgt_folder}')
  print(f'Now processing video {filename}...')
  if proc_keyframes:
    vf.extract_keyframes(f'{srcpath}{filename}',output_dir_keyframes=f'{tgt_folder}')
    savepath = f'{destpath}{name_keyframes_as}_v{num}_kf'
    #---#
    while os.path.exists(f'{savepath}.zip'):
      #print(f'{savepath}.zip already exists...')
      num = num+1
      savepath = f'{destpath}{name_keyframes_as}_v{num}_kf'
    #---#
    shutil.make_archive(savepath,'zip' , f'{tgt_folder}')
    #from moviepy.editor import VideoFileClip
  if proc_audio:
    from moviepy.editor import VideoFileClip
    # Load the WebM file
    video = VideoFileClip(f"{srcpath}{filename}")

    # Extract audio and save as MP3 (or WAV, etc.)
    audio = video.audio
    savepath = f"{destpath}_audio_v{num}.mp3"

    while os.path.exists(savepath):
      num = num+1
      savepath= f"{destpath}_audio_v{num}.mp3"
    #----#
    if audio:
      audio.write_audiofile(f'{savepath}')
      # Close the files to free resources
      audio.close()
      video.close()
  #----#
  if delete_mp4_when_done: os.remove(f'{srcpath}{filename}')
  num = num+1


In [ ]:

drive_folder_name = 'my_zip_folder' # @param {type:'string'}

%cd /content/
!zip -r /content/drive/MyDrive/{drive_folder_name}.zip /content/tmp

In [ ]:
from google.colab import runtime
#runtime.unassign()


